In [1]:
!pip  install pm4py
!pip install python-Levenshtein
!pip install scikit-learn
!pip install paretoset

  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 28.9 MB/s eta 0:00:00
  Created wheel for intervaltree: filename=intervaltree-3.1.0-py2.py3-none-any.whl size=26098 sha256=cc6c3d7010e970d9d633e747a340a618279020b87125f1eed894330807fd89aa
  Stored in directory: /root/.cache/pip/wheels/31/d7/d9/eec6891f78cac19a693bd40ecb8365d2f4613318c145ec9816
Successfully built intervaltree
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 161.7/161.7 kB 3.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 42.5 MB/s eta 0:00:00


In [2]:
import pm4py
import cudf
import cupy as cp
import numpy as np
import sklearn
from sklearn.cluster import DBSCAN as SklearnDBSCAN
from sklearn.cluster import KMeans
from sklearn.cluster import AgglomerativeClustering
from sklearn.metrics import silhouette_score, pairwise_distances
from sklearn.manifold import TSNE
from pm4py.objects.log.importer.xes import importer as xes_importer
from pm4py.algo.discovery.alpha import algorithm as alpha_miner
from pm4py.algo.conformance.tokenreplay import algorithm as token_replay
from pm4py.algo.evaluation.precision import algorithm as precision_evaluator
from pm4py.algo.evaluation.generalization import algorithm as generalization_evaluator
from collections import Counter
from Levenshtein import distance as levenshtein_distance
import time
import cupyx.scipy.sparse as cusp
import concurrent.futures as cf
import math
import pandas as pd
import os
import warnings
try:
    from numba import cuda
    CUDA_AVAILABLE = cuda.is_available()
except ImportError as e:
    print(f"Numba import error: {e}")
    CUDA_AVAILABLE = False
except Exception as e:
    print(f"CUDA availability check failed: {e}")
    CUDA_AVAILABLE = False

warnings.filterwarnings('ignore')

# Disable cudf.pandas acceleration
os.environ["CUDF_PANDAS_ACCELERATE"] = "false"

def setup_environment():
    """Set up environment and print package versions."""
    try:
        print(f"CUDA Available: {CUDA_AVAILABLE}")
        if CUDA_AVAILABLE:
            print(f"Using {cp.cuda.runtime.getDeviceCount()} GPU(s) with CUDA...")
        else:
            print("CUDA not available. Falling back to CPU-based methods (A1, A2 only).")
        print("Package Versions:")
        print(f"pandas: {pd.__version__}")
        print(f"scikit-learn: {sklearn.__version__}")
        print(f"numpy: {np.__version__}")
        print(f"pm4py: {pm4py.__version__}")
        print(f"cudf: {cudf.__version__}")
        print(f"cupy: {cp.__version__}")
        if CUDA_AVAILABLE:
            import numba
            print(f"numba: {numba.__version__}")
    except NameError as e:
        print(f"Error in setup_environment: {e}")
        print("Ensure all required libraries are installed: pandas, scikit-learn, numpy, pm4py, cudf, cupy, numba")
        raise

def load_event_log(file_path, max_traces=10000):
    """Load and process the event log from an XES file, limiting to max_traces."""
    print(f"Loading: {file_path}...")
    start_time = time.time()
    try:
        log = xes_importer.apply(file_path)
    except Exception as e:
        print(f"Error loading {file_path}: {e}")
        return None, None, None, 0
    print(f"Completed loading {file_path}: {time.time() - start_time:.2f}s")
    
    n_traces = len(log)
    print(f"Total traces: {n_traces}")
    
    # Split log if too large
    logs = []
    if n_traces > 12000:
        print(f"Splitting log into subsets of {max_traces} traces...")
        for i in range(0, n_traces, max_traces):
            subset_log = pm4py.objects.log.obj.EventLog(log[i:i + max_traces])
            logs.append(subset_log)
    else:
        logs.append(log)
    
    processed_logs = []
    for idx, sub_log in enumerate(logs):
        print(f"Processing subset {idx + 1}/{len(logs)}...")
        traces = [tuple(event["concept:name"] for event in trace) for trace in sub_log]
        unique_activities = sorted(set().union(*[set(trace) for trace in traces]))
        n_traces_sub = len(traces)
        processed_logs.append((sub_log, traces, unique_activities, n_traces_sub))
        print(f"Subset {idx + 1}: {n_traces_sub} traces, {len(unique_activities)} unique activities")
    
    return processed_logs

def compute_quality_metrics():
    """Define functions for computing quality metrics."""
    def compute_fitness(net, initial_marking, final_marking, trace_log):
        try:
            replayed_traces = token_replay.apply(trace_log, net, initial_marking, final_marking)
            fitness = sum(t["trace_fitness"] for t in replayed_traces) / len(replayed_traces)
            return fitness
        except:
            return 0

    def compute_simplicity(net):
        try:
            num_transitions = len(net.transitions)
            num_places = len(net.places)
            return num_transitions + num_places
        except:
            return 0

    def compute_precision(net, initial_marking, final_marking, trace_log):
        try:
            precision = precision_evaluator.apply(
                trace_log, net, initial_marking, final_marking,
                variant=precision_evaluator.Variants.ETCONFORMANCE_TOKEN
            )
            return precision
        except:
            return 0

    def compute_generalization(net, initial_marking, final_marking, trace_log):
        try:
            generalization = generalization_evaluator.apply(trace_log, net, initial_marking, final_marking)
            return generalization
        except:
            return 0

    def compute_silhouette_index(data, labels, metric='euclidean', use_gpu=True):
        print("Computing: Silhouette index...")
        start_time = time.time()
        data = cp.asarray(data) if use_gpu else np.asarray(data)
        labels = cp.asarray(labels) if use_gpu else np.asarray(labels)
        
        unique_labels = cp.unique(labels)
        n_clusters = len(unique_labels) - (1 if -1 in unique_labels else 0)
        
        if n_clusters < 2:
            print("Warning: Need at least 2 clusters for Silhouette Index.")
            return -1
        
        dist_matrix = data if metric == 'precomputed' else pairwise_distances(
            data.get() if use_gpu else data, metric=metric
        )
        dist_matrix = cp.asarray(dist_matrix) if use_gpu else dist_matrix
        
        silhouette_scores = []
        for i in range(len(labels)):
            if labels[i] == -1:
                continue
            same_cluster = (labels == labels[i])
            a_x = cp.mean(dist_matrix[i, same_cluster]) if cp.sum(same_cluster) > 1 else 0
            b_x = cp.inf
            for label in unique_labels:
                if label == labels[i] or label == -1:
                    continue
                other_cluster = (labels == label)
                if cp.sum(other_cluster) > 0:
                    b_x = min(b_x, cp.mean(dist_matrix[i, other_cluster]))
            s_x = 0 if a_x == 0 and b_x == 0 else (b_x - a_x) / max(a_x, b_x)
            silhouette_scores.append(float(s_x.get() if use_gpu else s_x))
        
        silhouette_avg = np.mean(silhouette_scores) if silhouette_scores else -1
        print(f"Completed Silhouette Index: {silhouette_avg:.4f} (Time: {time.time() - start_time:.2f}s)")
        return silhouette_avg
    
    return {
        "fitness": compute_fitness,
        "simplicity": compute_simplicity,
        "precision": compute_precision,
        "generalization": compute_generalization,
        "silhouette": compute_silhouette_index
    }

def compute_feature_vectors(traces, unique_activities, n_traces):
    """Compute feature vectors for different methods."""
    def bag_of_activities():
        print("Running: Computing vectors for Bag-of-activities (A1)...")
        start_time = time.time()
        vectors = cp.zeros((n_traces, len(unique_activities)))
        for i, trace in enumerate(traces):
            counter = Counter(trace)
            for j, activity in enumerate(unique_activities):
                vectors[i, j] = counter[activity]
        print(f"Completed A1: {time.time() - start_time:.2f}s")
        return vectors, "A1"

    def k_gram_model(k=3):
        print("Running: Computing vectors for k-gram model (A2)...")
        start_time = time.time()
        k_grams_set = set()
        for trace in traces:
            for i in range(len(trace) - k + 1):
                k_grams_set.add(trace[i:i+k])
        k_grams_list = sorted(k_grams_set)
        vectors = cp.zeros((n_traces, len(k_grams_list)))
        for i, trace in enumerate(traces):
            trace_k_grams = Counter([trace[j:j+k] for j in range(len(trace) - k + 1)])
            for j, k_gram in enumerate(k_grams_list):
                vectors[i, j] = trace_k_grams[k_gram]
        print(f"Completed A2: {time.time() - start_time:.2f}s")
        return vectors, "A2"

    def levenshtein_distance_matrix(chunk_size=10000):
        if not CUDA_AVAILABLE:
            print("Skipping A3 (Levenshtein Distance): CUDA not available.")
            return None, "A3"
        print("Running: Computing Levenshtein distance matrix on multi-GPU (A3)...")
        start_time = time.time()
        n_chunks = math.ceil(n_traces / chunk_size)
        max_len = max(max(len(t) for t in traces), 100)
        act_to_idx = {act: idx for idx, act in enumerate(unique_activities)}
        traces_padded = cp.zeros((n_traces, max_len + 1), dtype=cp.float32)
        for i, trace in enumerate(traces):
            traces_padded[i, 0] = len(trace)
            for j, act in enumerate(trace):
                traces_padded[i, j + 1] = act_to_idx[act]

        @cuda.jit
        def levenshtein_kernel(s_batch, t_batch, distances):
            i = cuda.grid(1)
            if i < s_batch.shape[0] * t_batch.shape[0]:
                s_idx = i // t_batch.shape[0]
                t_idx = i % t_batch.shape[0]
                s_len = int(s_batch[s_idx, 0])
                t_len = int(t_batch[t_idx, 0])
                s = s_batch[s_idx, 1:s_len+1]
                t = t_batch[t_idx, 1:t_len+1]
                dp = cuda.local.array((100, 100), dtype=cp.float32)
                for m in range(s_len + 1):
                    for n in range(t_len + 1):
                        if m == 0 and n == 0:
                            dp[m, n] = 0
                        elif m == 0:
                            dp[m, n] = dp[m, n-1] + 1
                        elif n == 0:
                            dp[m, n] = dp[m-1, n] + 1
                        else:
                            sub_cost = 0 if s[m-1] == t[n-1] else 1
                            dp[m, n] = min(dp[m-1, n-1] + sub_cost, dp[m-1, n] + 1, dp[m, n-1] + 1)
                distances[s_idx, t_idx] = dp[s_len, t_len]

        def process_chunk(i, gpu_id):
            with cp.cuda.Device(gpu_id):
                start_idx = i * chunk_size
                end_idx = min((i + 1) * chunk_size, n_traces)
                s_batch = traces_padded[start_idx:end_idx]
                t_batch = traces_padded
                distances = cp.zeros((s_batch.shape[0], t_batch.shape[0]), dtype=cp.float32)
                threads_per_block = 256
                blocks_per_grid = math.ceil((s_batch.shape[0] * t_batch.shape[0]) / threads_per_block)
                levenshtein_kernel[blocks_per_grid, threads_per_block](
                    s_batch, t_batch, distances
                )
                return distances

        dist_matrix_chunks = []
        n_gpus = cp.cuda.runtime.getDeviceCount() if CUDA_AVAILABLE else 1
        with cf.ThreadPoolExecutor(max_workers=n_gpus) as executor:
            futures = [executor.submit(process_chunk, i, i % n_gpus) for i in range(n_chunks)]
            for idx, future in enumerate(futures):
                dist_matrix_chunks.append(future.result())
                progress = (idx + 1) / n_chunks
                eta = (time.time() - start_time) / progress * (1 - progress)
                print(f"A3 Distance Matrix: Processed {idx+1}/{n_chunks} chunks ({progress*100:.2f}%), ETA: {eta:.2f}s")

        dist_matrix = cp.vstack(dist_matrix_chunks)
        dist_matrix_full = cp.zeros((n_traces, n_traces), dtype=cp.float32)
        dist_matrix_full[:dist_matrix.shape[0], :] = dist_matrix
        dist_matrix_full.T[:dist_matrix.shape[0], :] = dist_matrix
        dist_matrix_full = cp.maximum(dist_matrix_full, 0)
        nnz = cusp.csr_matrix(dist_matrix_full).nnz
        print(f"Completed A3: {time.time() - start_time:.2f}s")
        print(f"A3 Distance Matrix: Non-zero elements = {nnz}, Total elements = {n_traces * n_traces}")
        return dist_matrix_full, "A3"

    def get_3grams():
        activity_to_idx = {a: i for i, a in enumerate(unique_activities)}
        g3_counts = cp.zeros((len(unique_activities), len(unique_activities), len(unique_activities)), dtype=cp.int32)
        for trace in traces:
            for i in range(len(trace) - 2):
                x, a, y = trace[i:i+3]
                g3_counts[activity_to_idx[x], activity_to_idx[a], activity_to_idx[y]] += 1
        return g3_counts

    def compute_substitution_scores():
        print("Running: Computing Substitution Scores (Algorithm 1)...")
        start_time = time.time()
        n_activities = len(unique_activities)
        g3_counts = get_3grams()
        Xa = [set() for _ in range(n_activities)]
        for x_idx in range(n_activities):
            for a_idx in range(n_activities):
                for y_idx in range(n_activities):
                    if g3_counts[x_idx, a_idx, y_idx] > 0:
                        Xa[a_idx].add((x_idx, y_idx))
        C = cp.zeros((n_activities, n_activities), dtype=cp.float32)
        for a_idx in range(n_activities):
            for b_idx in range(n_activities):
                if a_idx == b_idx:
                    counts = g3_counts[:, a_idx, :]
                    C[a_idx, a_idx] = cp.sum(counts * (counts - 1) / 2)
                else:
                    Xab = Xa[a_idx] & Xa[b_idx]
                    for x_idx, y_idx in Xab:
                        C[a_idx, b_idx] += g3_counts[x_idx, a_idx, y_idx] * g3_counts[x_idx, b_idx, y_idx]
        NC = cp.sum(C)
        M = C / NC
        pa = cp.zeros(n_activities)
        for a_idx in range(n_activities):
            pa[a_idx] = M[a_idx, a_idx] + cp.sum(M[a_idx, :]) - M[a_idx, a_idx]
        E = cp.zeros((n_activities, n_activities))
        for a_idx in range(n_activities):
            for b_idx in range(n_activities):
                E[a_idx, b_idx] = pa[a_idx]**2 if a_idx == b_idx else 2 * pa[a_idx] * pa[b_idx]
        S = cp.log2(M / E)
        S = cp.where(cp.isinf(S) | cp.isnan(S), 0, S)
        print(f"Completed Substitution Scores: {time.time() - start_time:.2f}s")
        print(f"sub_scores: min={cp.min(S):.4f}, max={cp.max(S):.4f}, mean={cp.mean(S):.4f}")
        return S

    def compute_insertion_scores():
        print("Running: Computing Insertion Scores (Algorithm 2)...")
        start_time = time.time()
        n_activities = len(unique_activities)
        g3_counts = get_3grams()
        Xa = [set() for _ in range(n_activities)]
        for x_idx in range(n_activities):
            for a_idx in range(n_activities):
                for y_idx in range(n_activities):
                    if g3_counts[x_idx, a_idx, y_idx] > 0:
                        Xa[a_idx].add((x_idx, y_idx))
        count_right = cp.zeros((n_activities, n_activities), dtype=cp.float32)
        for a_idx in range(n_activities):
            for x_idx in range(n_activities):
                count_right[a_idx, x_idx] = cp.sum(g3_counts[x_idx, a_idx, :])
        norm = cp.sum(count_right, axis=1)
        pa = norm / cp.sum(norm)
        norm_count_right = count_right / norm[:, cp.newaxis]
        norm_count_right = cp.where(cp.isnan(norm_count_right), 0, norm_count_right)
        ins_scores = cp.log2(norm_count_right / (pa[:, cp.newaxis] * pa[cp.newaxis, :]))
        ins_scores = cp.where(cp.isinf(ins_scores) | cp.isnan(ins_scores), 0, ins_scores)
        print(f"Completed Insertion Scores: {time.time() - start_time:.2f}s")
        print(f"ins_scores: min={cp.min(ins_scores):.4f}, max={cp.max(ins_scores):.4f}, mean={cp.mean(ins_scores):.4f}")
        return ins_scores

    def generic_edit_distance_matrix(sub_scores, ins_scores, chunk_size=10000):
        if not CUDA_AVAILABLE:
            print("Skipping A4 (Generic Edit Distance): CUDA not available.")
            return None, "A4"
        print("Running: Computing Generic Edit Distance matrix on multi-GPU (A4)...")
        start_time = time.time()
        n_chunks = math.ceil(n_traces / chunk_size)
        max_len = max(max(len(t) for t in traces), 100)
        act_to_idx = {act: idx for idx, act in enumerate(unique_activities)}
        traces_padded = cp.zeros((n_traces, max_len + 1), dtype=cp.float32)
        for i, trace in enumerate(traces):
            traces_padded[i, 0] = len(trace)
            for j, act in enumerate(trace):
                traces_padded[i, j + 1] = act_to_idx[act]
        sub_scores_gpu = cp.asarray(sub_scores)
        ins_scores_gpu = cp.asarray(ins_scores)

        @cuda.jit
        def edit_distance_kernel(s_batch, t_batch, sub_scores, ins_scores, distances):
            i = cuda.grid(1)
            if i < s_batch.shape[0] * t_batch.shape[0]:
                s_idx = i // t_batch.shape[0]
                t_idx = i % t_batch.shape[0]
                s_len = s_batch[s_idx, 0]
                t_len = t_batch[t_idx, 0]
                s = s_batch[s_idx, 1:int(s_len+1)]
                t = t_batch[t_idx, 1:int(t_len+1)]
                dp = cuda.local.array((100, 100), dtype=cp.float32)
                for m in range(int(s_len) + 1):
                    for n in range(int(t_len) + 1):
                        if m == 0 and n == 0:
                            dp[m, n] = 0
                        elif m == 0:
                            dp[m, n] = dp[m, n-1] + max(1.0, abs(ins_scores[int(t[n-1]), int(t[n-1])]))
                        elif n == 0:
                            dp[m, n] = dp[m-1, n] + max(1.0, abs(ins_scores[int(s[m-1]), int(s[m-1])]))
                        else:
                            sub_cost = 0 if s[m-1] == t[n-1] else max(1.0, abs(sub_scores[int(s[m-1]), int(t[n-1])]))
                            del_cost = max(1.0, abs(ins_scores[int(s[m-1]), int(s[m-1])]))
                            ins_cost = max(1.0, abs(ins_scores[int(t[n-1]), int(t[n-1])]))
                            dp[m, n] = min(dp[m-1, n-1] + sub_cost, dp[m-1, n] + del_cost, dp[m, n-1] + ins_cost)
                distances[s_idx, t_idx] = dp[int(s_len), int(t_len)]

        def process_chunk(i, gpu_id):
            with cp.cuda.Device(gpu_id):
                start_idx = i * chunk_size
                end_idx = min((i + 1) * chunk_size, n_traces)
                s_batch = traces_padded[start_idx:end_idx]
                t_batch = traces_padded
                distances = cp.zeros((s_batch.shape[0], t_batch.shape[0]), dtype=cp.float32)
                threads_per_block = 256
                blocks_per_grid = math.ceil((s_batch.shape[0] * t_batch.shape[0]) / threads_per_block)
                edit_distance_kernel[blocks_per_grid, threads_per_block](
                    s_batch, t_batch, sub_scores_gpu, ins_scores_gpu, distances
                )
                return distances

        dist_matrix_chunks = []
        n_gpus = cp.cuda.runtime.getDeviceCount() if CUDA_AVAILABLE else 1
        with cf.ThreadPoolExecutor(max_workers=n_gpus) as executor:
            futures = [executor.submit(process_chunk, i, i % n_gpus) for i in range(n_chunks)]
            for idx, future in enumerate(futures):
                dist_matrix_chunks.append(future.result())
                progress = (idx + 1) / n_chunks
                eta = (time.time() - start_time) / progress * (1 - progress)
                print(f"A4 Distance Matrix: Processed {idx+1}/{n_chunks} chunks ({progress*100:.2f}%), ETA: {eta:.2f}s")
        
        dist_matrix = cp.vstack(dist_matrix_chunks)
        dist_matrix_full = cp.zeros((n_traces, n_traces), dtype=cp.float32)
        dist_matrix_full[:dist_matrix.shape[0], :] = dist_matrix
        dist_matrix_full.T[:dist_matrix.shape[0], :] = dist_matrix
        dist_matrix_full = cp.maximum(dist_matrix_full, 0)
        print(f"Completed Distance Matrix: {time.time() - start_time:.2f}s")
        nnz = cusp.csr_matrix(dist_matrix_full).nnz
        print(f"A4 Distance Matrix: Non-zero elements = {nnz}, Total elements = {n_traces * n_traces}")
        return dist_matrix_full, "A4"

    def log_skeleton_distance_matrix(chunk_size=None):
        if not CUDA_AVAILABLE:
            print("Skipping A5 (Log Skeleton): CUDA not available.")
            return None, "A5"
        print("Running: Computing Log Skeleton distance matrix on multi-GPU (A5)...")
        start_time = time.time()

        # Preprocess traces
        alpha, omega = "α", "ω"
        extended_activities = [alpha] + unique_activities + [omega]
        act_to_idx = {act: idx for idx, act in enumerate(extended_activities)}
        extended_traces = [[alpha] + list(trace) + [omega] for trace in traces]
        n_activities = len(extended_activities)
        max_len = max(max(len(t) for t in extended_traces), 100)
        if max_len > 100:
            raise ValueError(f"Trace length {max_len} exceeds maximum supported length (100). Increase kernel array size.")

        traces_array = cp.zeros((n_traces, max_len + 1), dtype=cp.int32)
        for i, trace in enumerate(extended_traces):
            traces_array[i, 0] = len(trace)
            for j, act in enumerate(trace):
                traces_array[i, j + 1] = act_to_idx[act]

        # Compute relations
        print("Computing: Log Skeleton relations...")
        rel_start_time = time.time()

        if chunk_size is None:
            gpu_mem = cp.cuda.runtime.memGetInfo()[0] // (1024 ** 2) if CUDA_AVAILABLE else 1024
            est_mem_per_trace = max_len * 4 / (1024 ** 2)
            chunk_size = max(1000, int(gpu_mem * 0.5 / est_mem_per_trace))
            print(f"Dynamic chunk_size set to {chunk_size} based on GPU memory ({gpu_mem} MB free)")

        @cuda.jit
        def equivalence_kernel(traces_array, counts, R_eq):
            t_idx, a_idx, b_idx = cuda.grid(3)
            if t_idx < traces_array.shape[0] and a_idx < R_eq.shape[0] and b_idx < R_eq.shape[1]:
                if a_idx == b_idx:
                    cuda.atomic.add(R_eq, (a_idx, b_idx), 1)
                else:
                    trace_len = int(traces_array[t_idx, 0])
                    count_a = 0
                    count_b = 0
                    for i in range(trace_len):
                        if int(traces_array[t_idx, i + 1]) == a_idx:
                            count_a += 1
                        if int(traces_array[t_idx, i + 1]) == b_idx:
                            count_b += 1
                    if count_a == count_b:
                        cuda.atomic.add(R_eq, (a_idx, b_idx), 1)

        @cuda.jit
        def always_after_kernel(traces_array, R_aa):
            t_idx, a_idx, b_idx = cuda.grid(3)
            if t_idx < traces_array.shape[0] and a_idx < R_aa.shape[0] and b_idx < R_aa.shape[1] and a_idx != b_idx:
                trace_len = int(traces_array[t_idx, 0])
                idx_a = cuda.local.array(100, dtype=cp.int32)
                idx_b = cuda.local.array(100, dtype=cp.int32)
                a_count = 0
                b_count = 0
                for i in range(trace_len):
                    if int(traces_array[t_idx, i + 1]) == a_idx and a_count < 100:
                        idx_a[a_count] = i
                        a_count += 1
                    if int(traces_array[t_idx, i + 1]) == b_idx and b_count < 100:
                        idx_b[b_count] = i
                        b_count += 1
                if a_count > 0 and b_count > 0:
                    if idx_b[0] > idx_a[a_count - 1]:
                        cuda.atomic.add(R_aa, (a_idx, b_idx), 1)

        @cuda.jit
        def always_before_kernel(traces_array, R_ab):
            t_idx, a_idx, b_idx = cuda.grid(3)
            if t_idx < traces_array.shape[0] and a_idx < R_ab.shape[0] and b_idx < R_ab.shape[1] and a_idx != b_idx:
                trace_len = int(traces_array[t_idx, 0])
                idx_a = cuda.local.array(100, dtype=cp.int32)
                idx_b = cuda.local.array(100, dtype=cp.int32)
                a_count = 0
                b_count = 0
                for i in range(trace_len):
                    if int(traces_array[t_idx, i + 1]) == a_idx and a_count < 100:
                        idx_a[a_count] = i
                        a_count += 1
                    if int(traces_array[t_idx, i + 1]) == b_idx and b_count < 100:
                        idx_b[b_count] = i
                        b_count += 1
                if a_count > 0 and b_count > 0:
                    if idx_a[a_count - 1] < idx_b[0]:
                        cuda.atomic.add(R_ab, (a_idx, b_idx), 1)

        @cuda.jit
        def never_together_kernel(traces_array, R_nt):
            t_idx, a_idx, b_idx = cuda.grid(3)
            if t_idx < traces_array.shape[0] and a_idx < R_nt.shape[0] and b_idx < R_nt.shape[1] and a_idx < b_idx:
                trace_len = int(traces_array[t_idx, 0])
                has_a = False
                has_b = False
                for i in range(trace_len):
                    if int(traces_array[t_idx, i + 1]) == a_idx:
                        has_a = True
                    if int(traces_array[t_idx, i + 1]) == b_idx:
                        has_b = True
                if not (has_a and has_b):
                    cuda.atomic.add(R_nt, (a_idx, b_idx), 1)
                    cuda.atomic.add(R_nt, (b_idx, a_idx), 1)

        @cuda.jit
        def directly_follows_kernel(traces_array, R_df):
            t_idx = cuda.grid(1)
            if t_idx < traces_array.shape[0]:
                trace_len = int(traces_array[t_idx, 0])
                for i in range(trace_len - 1):
                    a_idx = int(traces_array[t_idx, i + 1])
                    b_idx = int(traces_array[t_idx, i + 2])
                    cuda.atomic.add(R_df, (a_idx, b_idx), 1)

        @cuda.jit
        def log_skeleton_distance_kernel(s_batch, t_batch, R_eq, R_aa, R_ab, R_nt, R_df, C_min, C_max, distances):
            i = cuda.grid(1)
            if i < s_batch.shape[0] * t_batch.shape[0]:
                s_idx = i // t_batch.shape[0]
                t_idx = i % t_batch.shape[0]
                s_len = int(s_batch[s_idx, 0])
                t_len = int(t_batch[t_idx, 0])
                s = s_batch[s_idx, 1:s_len+1]
                t = t_batch[t_idx, 1:t_len+1]
                distance = 0.0

                # R_eq
                for a_idx in range(R_eq.shape[0]):
                    for b_idx in range(a_idx, R_eq.shape[1]):
                        if R_eq[a_idx, b_idx]:
                            count_s_a = 0
                            count_s_b = 0
                            count_t_a = 0
                            count_t_b = 0
                            for m in range(s_len):
                                if int(s[m]) == a_idx:
                                    count_s_a += 1
                                if int(s[m]) == b_idx:
                                    count_s_b += 1
                            for n in range(t_len):
                                if int(t[n]) == a_idx:
                                    count_t_a += 1
                                if int(t[n]) == b_idx:
                                    count_t_b += 1
                            if (count_s_a == count_s_b) != (count_t_a == count_t_b):
                                distance += 1.0

                # R_aa and R_ab
                for a_idx in range(R_aa.shape[0]):
                    for b_idx in range(R_aa.shape[1]):
                        if a_idx == b_idx:
                            continue
                        idx_s_a = cuda.local.array(50, dtype=cp.int32)
                        idx_s_b = cuda.local.array(50, dtype=cp.int32)
                        idx_t_a = cuda.local.array(50, dtype=cp.int32)
                        idx_t_b = cuda.local.array(50, dtype=cp.int32)
                        s_a_count = 0
                        s_b_count = 0
                        t_a_count = 0
                        t_b_count = 0
                        for m in range(s_len):
                            if int(s[m]) == a_idx and s_a_count < 50:
                                idx_s_a[s_a_count] = m
                                s_a_count += 1
                            if int(s[m]) == b_idx and s_b_count < 50:
                                idx_s_b[s_b_count] = m
                                s_b_count += 1
                        for n in range(t_len):
                            if int(t[n]) == a_idx and t_a_count < 50:
                                idx_t_a[t_a_count] = n
                                t_a_count += 1
                            if int(t[n]) == b_idx and t_b_count < 50:
                                idx_t_b[t_b_count] = n
                                t_b_count += 1
                        # R_aa
                        if R_aa[a_idx, b_idx]:
                            after_s = s_a_count == 0 or s_b_count == 0 or idx_s_b[0] > idx_s_a[s_a_count - 1]
                            after_t = t_a_count == 0 or t_b_count == 0 or idx_t_b[0] > idx_t_a[t_a_count - 1]
                            if after_s != after_t:
                                distance += 1.0
                        # R_ab
                        if R_ab[a_idx, b_idx]:
                            before_s = s_a_count == 0 or s_b_count == 0 or idx_s_a[s_a_count - 1] < idx_s_b[0]
                            before_t = t_a_count == 0 or t_b_count == 0 or idx_t_a[t_a_count - 1] < idx_t_b[0]
                            if before_s != before_t:
                                distance += 1.0

                # R_nt
                for a_idx in range(R_nt.shape[0]):
                    for b_idx in range(a_idx + 1, R_nt.shape[1]):
                        if R_nt[a_idx, b_idx]:
                            has_s_a = False
                            has_s_b = False
                            has_t_a = False
                            has_t_b = False
                            for m in range(s_len):
                                if int(s[m]) == a_idx:
                                    has_s_a = True
                                if int(s[m]) == b_idx:
                                    has_s_b = True
                            for n in range(t_len):
                                if int(t[n]) == a_idx:
                                    has_t_a = True
                                if int(t[n]) == b_idx:
                                    has_t_b = True
                            if (has_s_a and has_s_b) != (has_t_a and has_t_b):
                                distance += 1.0

                # R_df
                for a_idx in range(R_df.shape[0]):
                    for b_idx in range(R_df.shape[1]):
                        if R_df[a_idx, b_idx] > 0:
                            df_s = 0
                            df_t = 0
                            for m in range(s_len - 1):
                                if int(s[m]) == a_idx and int(s[m + 1]) == b_idx:
                                    df_s += 1
                            for n in range(t_len - 1):
                                if int(t[n]) == a_idx and int(t[n + 1]) == b_idx:
                                    df_t += 1
                            distance += abs(df_s - df_t) * 0.1

                # Counters
                for a_idx in range(len(C_min)):
                    count_s = 0
                    count_t = 0
                    for m in range(s_len):
                        if int(s[m]) == a_idx:
                            count_s += 1
                    for n in range(t_len):
                        if int(t[n]) == a_idx:
                            count_t += 1
                    if not (C_min[a_idx] <= count_s <= C_max[a_idx] and C_min[a_idx] <= count_t <= C_max[a_idx]):
                        distance += abs(count_s - count_t) * 0.1

                distances[s_idx, t_idx] = distance

        R_eq = cp.zeros((n_activities, n_activities), dtype=cp.int32)
        threads_per_block = (8, 8, 8)
        blocks_per_grid = (
            math.ceil(n_traces / threads_per_block[0]),
            math.ceil(n_activities / threads_per_block[1]),
            math.ceil(n_activities / threads_per_block[2])
        )
        equivalence_kernel[blocks_per_grid, threads_per_block](traces_array, cp.zeros((n_traces, n_activities), dtype=cp.int32), R_eq)
        R_eq = (R_eq == n_traces).astype(cp.bool_)
        R_eq |= R_eq.T

        R_aa = cp.zeros((n_activities, n_activities), dtype=cp.int32)
        always_after_kernel[blocks_per_grid, threads_per_block](traces_array, R_aa)
        R_aa = (R_aa == n_traces).astype(cp.bool_)

        R_ab = cp.zeros((n_activities, n_activities), dtype=cp.int32)
        always_before_kernel[blocks_per_grid, threads_per_block](traces_array, R_ab)
        R_ab = (R_ab == n_traces).astype(cp.bool_)

        R_nt = cp.zeros((n_activities, n_activities), dtype=cp.int32)
        never_together_kernel[blocks_per_grid, threads_per_block](traces_array, R_nt)
        R_nt = (R_nt == n_traces).astype(cp.bool_)

        R_df = cp.zeros((n_activities, n_activities), dtype=cp.int32)
        threads_per_block_df = 256
        blocks_per_grid_df = math.ceil(n_traces / threads_per_block_df)
        directly_follows_kernel[blocks_per_grid_df, threads_per_block_df](traces_array, R_df)

        counts = cp.zeros((n_traces, n_activities), dtype=cp.int32)
        for i in range(n_traces):
            trace_len = int(traces_array[i, 0])
            for j in range(trace_len):
                act_idx = int(traces_array[i, j + 1])
                counts[i, act_idx] += 1
        C_min = cp.min(counts, axis=0)
        C_max = cp.max(counts, axis=0)

        print(f"Completed relations computation: {time.time() - rel_start_time:.2f}s")

        # Compute distance matrix
        n_chunks = math.ceil(n_traces / chunk_size)
        traces_padded = traces_array

        def process_chunk(i, gpu_id):
            with cp.cuda.Device(gpu_id):
                start_idx = i * chunk_size
                end_idx = min((i + 1) * chunk_size, n_traces)
                s_batch = traces_padded[start_idx:end_idx]
                t_batch = traces_padded
                distances = cp.zeros((s_batch.shape[0], t_batch.shape[0]), dtype=cp.float32)
                threads_per_block = 256
                blocks_per_grid = math.ceil((s_batch.shape[0] * t_batch.shape[0]) / threads_per_block)
                log_skeleton_distance_kernel[blocks_per_grid, threads_per_block](
                    s_batch, t_batch, R_eq, R_aa, R_ab, R_nt, R_df, C_min, C_max, distances
                )
                return distances

        dist_matrix_chunks = []
        n_gpus = cp.cuda.runtime.getDeviceCount() if CUDA_AVAILABLE else 1
        with cf.ThreadPoolExecutor(max_workers=n_gpus) as executor:
            futures = [executor.submit(process_chunk, i, i % n_gpus) for i in range(n_chunks)]
            for idx, future in enumerate(futures):
                dist_matrix_chunks.append(future.result())
                progress = (idx + 1) / n_chunks
                eta = (time.time() - start_time) / progress * (1 - progress)
                print(f"A5 Distance Matrix: Processed {idx+1}/{n_chunks} chunks ({progress*100:.2f}%), ETA: {eta:.2f}s")

        dist_matrix = cp.vstack(dist_matrix_chunks)
        dist_matrix_full = cp.zeros((n_traces, n_traces), dtype=cp.float32)
        dist_matrix_full[:dist_matrix.shape[0], :] = dist_matrix
        dist_matrix_full.T[:dist_matrix.shape[0], :] = dist_matrix
        dist_matrix_full = cp.maximum(dist_matrix_full, 0)
        nnz = cusp.csr_matrix(dist_matrix_full).nnz
        print(f"Completed A5: {time.time() - start_time:.2f}s")
        print(f"A5 Distance Matrix: Non-zero elements = {nnz}, Total elements = {n_traces * n_traces}")
        return dist_matrix_full, "A5"

    methods = [
        bag_of_activities(),
        k_gram_model()
    ]
    if CUDA_AVAILABLE:
        try:
            sub_scores = compute_substitution_scores()
            ins_scores = compute_insertion_scores()
            methods.extend([
                levenshtein_distance_matrix(),
                generic_edit_distance_matrix(sub_scores, ins_scores),
                log_skeleton_distance_matrix()
            ])
        except Exception as e:
            print(f"Error in CUDA-based methods (A3, A4, A5): {e}")
            print("Falling back to CPU-based methods (A1, A2 only).")
    else:
        print("CUDA not available. Using CPU-based methods (A1, A2 only).")
    
    # Filter out None results (failed methods)
    methods = [(vec, name) for vec, name in methods if vec is not None]
    return methods

def estimate_eps(data):
    """Estimate eps parameter for DBSCAN."""
    try:
        if hasattr(data, 'toarray'):
            dist_array = data.toarray().get()
        elif hasattr(data, 'get'):
            dist_array = data.get()
        else:
            dist_array = cp.pdist(data).get()
        positive_dists = dist_array[dist_array > 0]
        return np.mean(positive_dists) * 0.05 if len(positive_dists) > 0 else 0.1
    except Exception as e:
        print(f"Error in estimate_eps: {e}")
        return 0.1

def extract_dataset_characteristics(log, traces, unique_activities, n_traces):
    """Extract characteristics of the dataset."""
    try:
        avg_trace_length = np.mean([len(trace) for trace in traces])
        max_trace_length = max(len(trace) for trace in traces)
        num_events = sum(len(trace) for trace in traces)
        return {
            'Dataset': '',
            'n_traces': n_traces,
            'n_unique_activities': len(unique_activities),
            'avg_trace_length': avg_trace_length,
            'max_trace_length': max_trace_length,
            'num_events': num_events
        }
    except Exception as e:
        print(f"Error in extract_dataset_characteristics: {e}")
        return {
            'Dataset': '',
            'n_traces': n_traces,
            'n_unique_activities': len(unique_activities),
            'avg_trace_length': 0,
            'max_trace_length': 0,
            'num_events': 0
        }

def select_best_combination(results, dataset_characteristics):
    """Select the best clustering combination based on composite score."""
    try:
        df = pd.DataFrame(results)
        if df.empty:
            print("No results to select best combination.")
            return None
        
        # Compute composite score
        weights = {'Silhouette': 0.4, 'Fitness': 0.3, 'Precision': 0.2, 'Generalization': 0.1}
        def compute_composite_score(row):
            normalized = {}
            for metric in ['Silhouette', 'Fitness', 'Precision', 'Generalization']:
                values = df[metric]
                min_val, max_val = values.min(), values.max()
                normalized[metric] = (row[metric] - min_val) / (max_val - min_val + 1e-10)
            return sum(normalized[metric] * weights[metric] for metric in weights)
        
        df['Composite_Score'] = df.apply(compute_composite_score, axis=1)
        best_combination_idx = df['Composite_Score'].idxmax()
        best_combination = df.loc[best_combination_idx].to_dict()
        best_combination.update(dataset_characteristics)
        return best_combination
    except Exception as e:
        print(f"Error in select_best_combination: {e}")
        return None

def perform_clustering_and_evaluation(log, traces, methods, metrics, dataset_name, subset_idx):
    """Perform clustering and evaluate results."""
    results = []
    for method, name in methods:
        print(f"Running: Clustering for {name} (Dataset: {dataset_name}, Subset: {subset_idx})...")
        start_time = time.time()
        
        try:
            eps = estimate_eps(method)
            print(f"Estimated eps for {name}: {eps:.4f}")
            
            if name in ["A1", "A2"]:
                clustering_dbscan = SklearnDBSCAN(eps=eps, min_samples=5)
                labels_dbscan = clustering_dbscan.fit_predict(method.get())
                data_for_kmeans = method.get()
            else:
                dist_matrix = cp.maximum(method, 0)
                clustering_dbscan = SklearnDBSCAN(eps=eps, min_samples=5, metric="precomputed")
                labels_dbscan = clustering_dbscan.fit_predict(dist_matrix.get())
                data_for_kmeans = TSNE(n_components=2, metric="precomputed", init="random", random_state=42).fit_transform(dist_matrix.get())
            
            unique_labels_dbscan = np.unique(labels_dbscan)
            n_clusters_dbscan = len(unique_labels_dbscan) - (1 if -1 in unique_labels_dbscan else 0)
            print(f"Clusters found for {name} (DBSCAN): {n_clusters_dbscan}")
            
            labels_kmeans = labels_dbscan
            labels_hierarchical = labels_dbscan
            if n_clusters_dbscan > 1:
                kmeans = KMeans(n_clusters=n_clusters_dbscan, random_state=42)
                labels_kmeans = kmeans.fit_predict(data_for_kmeans)
                hierarchical = AgglomerativeClustering(n_clusters=n_clusters_dbscan)
                labels_hierarchical = hierarchical.fit_predict(data_for_kmeans)
            
            silhouette_dbscan = metrics["silhouette"](method if name in ["A1", "A2"] else dist_matrix, 
                                                    labels_dbscan, 
                                                    metric='euclidean' if name in ["A1", "A2"] else 'precomputed')
            silhouette_kmeans = metrics["silhouette"](data_for_kmeans, labels_kmeans, metric='euclidean') if n_clusters_dbscan > 1 else -1
            silhouette_hierarchical = metrics["silhouette"](data_for_kmeans, labels_hierarchical, metric='euclidean') if n_clusters_dbscan > 1 else -1
            
            for algo, labels in [("DBSCAN", labels_dbscan), ("K-means", labels_kmeans), ("Hierarchical", labels_hierarchical)]:
                unique_labels = np.unique(labels)
                n_clusters = len(unique_labels) - (1 if -1 in unique_labels else 0)
                clustered_logs = [pm4py.objects.log.obj.EventLog([trace for trace, label in zip(log, labels) if label == i])
                                 for i in unique_labels if i != -1]
                
                fitness_scores = []
                simplicity_scores = []
                precision_scores = []
                generalization_scores = []
                
                for i, cluster_log in enumerate(clustered_logs):
                    if len(cluster_log) == 0:
                        continue
                    print(f"Mining cluster {i+1}/{len(clustered_logs)} for {name} ({algo})...")
                    try:
                        net, im, fm = alpha_miner.apply(cluster_log)
                        fitness_scores.append(metrics["fitness"](net, im, fm, cluster_log))
                        simplicity_scores.append(metrics["simplicity"](net))
                        precision_scores.append(metrics["precision"](net, im, fm, cluster_log))
                        generalization_scores.append(metrics["generalization"](net, im, fm, cluster_log))
                    except Exception as e:
                        print(f"Error mining cluster {i+1} for {name} ({algo}): {e}")
                        continue
                
                results.append({
                    'Dataset': dataset_name,
                    'Subset': subset_idx,
                    'Method': name,
                    'Algorithm': algo,
                    'Fitness': np.mean(fitness_scores) if fitness_scores else 0,
                    'Simplicity': np.mean(simplicity_scores) if simplicity_scores else 0,
                    'Precision': np.mean(precision_scores) if precision_scores else 0,
                    'Generalization': np.mean(generalization_scores) if generalization_scores else 0,
                    'N_Clusters': n_clusters,
                    'Silhouette': silhouette_dbscan if algo == "DBSCAN" else (silhouette_kmeans if algo == "K-means" else silhouette_hierarchical),
                    'Time': time.time() - start_time
                })
        except Exception as e:
            print(f"Error in clustering for {name} (Dataset: {dataset_name}, Subset: {subset_idx}): {e}")
            continue
    
    return results

def main_part1(file_path):
    """Process a single XES file, evaluate clustering combinations, and save best results."""
    setup_environment()
    metrics = compute_quality_metrics()
    all_best_results = []
    
    # Check if file exists
    if not os.path.exists(file_path):
        print(f"File not found: {file_path}")
        return
    
    # Process the specified file
    dataset_name = os.path.basename(file_path)
    processed_logs = load_event_log(file_path)
    if not processed_logs:
        print(f"Failed to process {file_path}")
        return
    
    for subset_idx, (log, traces, unique_activities, n_traces) in enumerate(processed_logs):
        if n_traces == 0:
            print(f"Skipping empty subset {subset_idx + 1} for {dataset_name}")
            continue
        characteristics = extract_dataset_characteristics(log, traces, unique_activities, n_traces)
        characteristics['Dataset'] = f"{dataset_name}_subset_{subset_idx + 1}"
        
        try:
            methods = compute_feature_vectors(traces, unique_activities, n_traces)
            if not methods:
                print(f"No valid feature extraction methods for {dataset_name} subset {subset_idx + 1}")
                continue
            results = perform_clustering_and_evaluation(log, traces, methods, metrics, dataset_name, subset_idx + 1)
            if not results:
                print(f"No results for {dataset_name} subset {subset_idx + 1}")
                continue
            
            # Select best combination
            best_combination = select_best_combination(results, characteristics)
            if best_combination:
                all_best_results.append(best_combination)
                # Save results to CSV
                output_file = f"results_{dataset_name}_subset_{subset_idx + 1}.csv"
                pd.DataFrame([best_combination]).to_csv(output_file, index=False)
                print(f"Saved best combination for {dataset_name} subset {subset_idx + 1} to {output_file}")
                print(f"Best Combination: Method={best_combination['Method']}, Algorithm={best_combination['Algorithm']}")
                print(f"Metrics: Fitness={best_combination['Fitness']:.4f}, Simplicity={best_combination['Simplicity']:.4f}, "
                      f"Precision={best_combination['Precision']:.4f}, Generalization={best_combination['Generalization']:.4f}")
                print(f"Silhouette Index: {best_combination['Silhouette']:.4f}, Composite Score: {best_combination['Composite_Score']:.4f}")
        except Exception as e:
            print(f"Error processing {dataset_name} subset {subset_idx + 1}: {e}")
            continue
    
    # Save all best results to a summary CSV
    if all_best_results:
        pd.DataFrame(all_best_results).to_csv('all_best_combinations_part1.csv', index=False)
        print(f"All best combinations for {dataset_name} saved to 'all_best_combinations_part1.csv'")

if __name__ == "__main__":
    file_path = "/kaggle/input/event-log/DomesticDeclarations.xes"
    main_part1(file_path)

CUDA Available: True
Using 2 GPU(s) with CUDA...
Package Versions:
pandas: 2.2.3
scikit-learn: 1.2.2
numpy: 1.26.4
pm4py: 2.7.16
cudf: 25.02.02
cupy: 13.4.1
numba: 0.60.0
Loading: /kaggle/input/event-log/DomesticDeclarations.xes...


parsing log, completed traces ::   0%|          | 0/10500 [00:00<?, ?it/s]

Completed loading /kaggle/input/event-log/DomesticDeclarations.xes: 3.18s
Total traces: 10500
Processing subset 1/1...
Subset 1: 10500 traces, 17 unique activities
Running: Computing vectors for Bag-of-activities (A1)...
Completed A1: 2.51s
Running: Computing vectors for k-gram model (A2)...
Completed A2: 4.96s
Running: Computing Substitution Scores (Algorithm 1)...
Completed Substitution Scores: 3.80s
sub_scores: min=-6.4561, max=15.7130, mean=0.5499
Running: Computing Insertion Scores (Algorithm 2)...
Completed Insertion Scores: 5.86s
ins_scores: min=-4.5250, max=20.0495, mean=0.9644
Running: Computing Levenshtein distance matrix on multi-GPU (A3)...
A3 Distance Matrix: Processed 1/2 chunks (50.00%), ETA: 2.22s
A3 Distance Matrix: Processed 2/2 chunks (100.00%), ETA: 0.00s
Completed A3: 35.03s
A3 Distance Matrix: Non-zero elements = 80318486, Total elements = 110250000
Running: Computing Generic Edit Distance matrix on multi-GPU (A4)...
A4 Distance Matrix: Processed 1/2 chunks (50.00

replaying log with TBR, completed traces ::   0%|          | 0/3 [00:00<?, ?it/s]

Mining cluster 2/32 for A1 (DBSCAN)...


...

Mining cluster 32/32 for A5 (Hierarchical)...


replaying log with TBR, completed traces ::   0%|          | 0/18 [00:00<?, ?it/s]

replaying log with TBR, completed traces ::   0%|          | 0/36 [00:00<?, ?it/s]

replaying log with TBR, completed traces ::   0%|          | 0/18 [00:00<?, ?it/s]

Saved best combination for DomesticDeclarations.xes subset 1 to results_DomesticDeclarations.xes_subset_1.csv
Best Combination: Method=A3, Algorithm=DBSCAN
Metrics: Fitness=0.9377, Simplicity=12.0645, Precision=1.0000, Generalization=0.8004
Silhouette Index: 1.0000, Composite Score: 0.9465
All best combinations for DomesticDeclarations.xes saved to 'all_best_combinations_part1.csv'
